Lambda School Data Science

*Unit 2, Sprint 1, Module 2*

---

# Regression 2

## Assignment

You'll continue to **predict how much it costs to rent an apartment in NYC,** using the dataset from renthop.com.

- [x] Do train/test split. Use data from April & May 2016 to train. Use data from June 2016 to test.
- [x] Engineer at least two new features. (See below for explanation & ideas.)
- [x] Fit a linear regression model with at least two features.
- [x] Get the model's coefficients and intercept.
- [x] Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.
- [x] What's the best test MAE you can get? Share your score and features used with your cohort on Slack!
- [x] As always, commit your notebook to your fork of the GitHub repo.


#### [Feature Engineering](https://en.wikipedia.org/wiki/Feature_engineering)

> "Some machine learning projects succeed and some fail. What makes the difference? Easily the most important factor is the features used." — Pedro Domingos, ["A Few Useful Things to Know about Machine Learning"](https://homes.cs.washington.edu/~pedrod/papers/cacm12.pdf)

> "Coming up with features is difficult, time-consuming, requires expert knowledge. 'Applied machine learning' is basically feature engineering." — Andrew Ng, [Machine Learning and AI via Brain simulations](https://forum.stanford.edu/events/2011/2011slides/plenary/2011plenaryNg.pdf) 

> Feature engineering is the process of using domain knowledge of the data to create features that make machine learning algorithms work. 

#### Feature Ideas
- Does the apartment have a description?
- How long is the description?
- How many total perks does each apartment have?
- Are cats _or_ dogs allowed?
- Are cats _and_ dogs allowed?
- Total number of rooms (beds + baths)
- Ratio of beds to baths
- What's the neighborhood, based on address or latitude & longitude?

## Stretch Goals
- [ ] If you want more math, skim [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf),  Chapter 3.1, Simple Linear Regression, & Chapter 3.2, Multiple Linear Regression
- [ ] If you want more introduction, watch [Brandon Foltz, Statistics 101: Simple Linear Regression](https://www.youtube.com/watch?v=ZkjP5RJLQF4)
(20 minutes, over 1 million views)
- [ ] Add your own stretch goal(s) !

In [0]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
import numpy as np
import pandas as pd

# Read New York City apartment rental listing data
df = pd.read_csv(DATA_PATH+'apartments/renthop-nyc.csv')
assert df.shape == (49352, 34)

# Remove the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= np.percentile(df['price'], 0.5)) & 
        (df['price'] <= np.percentile(df['price'], 99.5)) & 
        (df['latitude'] >= np.percentile(df['latitude'], 0.05)) & 
        (df['latitude'] < np.percentile(df['latitude'], 99.95)) &
        (df['longitude'] >= np.percentile(df['longitude'], 0.05)) & 
        (df['longitude'] <= np.percentile(df['longitude'], 99.95))]

In [218]:
df.head()

bathrooms  bedrooms  ... wheelchair_access common_outdoor_space
0        1.5         3  ...                 0                    0
1        1.0         2  ...                 0                    0
2        1.0         1  ...                 0                    0
3        1.0         1  ...                 0                    0
4        1.0         4  ...                 0                    0

[5 rows x 34 columns]

In [219]:
import plotly.express as px

# convert 'created' to datetime format
df['created'] = pd.to_datetime(df['created'])

# convert 'interest_level' to int
interest_dict = {'low' : 1,
                 'medium' : 2,
                 'high' : 3}
df['interest_level'] = df['interest_level'].map(interest_dict)
px.scatter(df, x='interest_level', y='price', trendline='ols')

In [220]:
# create a (probably useless) 'distance_from_mean' value
mean_lat = df['latitude'].mean()
mean_long = df['longitude'].mean()
df['distance_from_mean'] = np.sqrt(np.power(df['latitude'] - mean_lat, 2) + 
                                   np.power(df['longitude'] - mean_long, 2))

px.scatter(df, x='distance_from_mean', y='price', trendline='ols')

In [221]:
from sklearn.linear_model import LinearRegression

# split up data:
start_date = '04-01-2016'
end_date = '06-1-2016'
train = df[(df['created'] >= start_date) & (df['created'] < end_date)]
test =  df[(df['created'] >= end_date)]

# train model:
features = ['bathrooms', 'bedrooms', 'distance_from_mean', 'interest_level']
target = 'price'
model = LinearRegression()
model.fit(train[features], train[target])



LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [222]:
# Get cooeficients and intercept:
model.intercept_, model.coef_
beta0 = model.intercept_
beta1, beta2, beta3, beta4 = model.coef_
print(f'y = {beta0} + {beta1}x1 + {beta2}x2 + {beta3}x3 + {beta4}x4')

y = 1725.7516005306031 + 1891.7866262515433x1 + 466.4319703104039x2 + -13979.02369435142x3 + -431.77335735370735x4


In [223]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

y_pred_train = model.predict(train[features])
y_pred_test = model.predict(test[features])

# rmse:
print("train root mean squared error:", np.sqrt(mean_squared_error(train[target], y_pred_train)))
print("test root mean squared error:", np.sqrt(mean_squared_error(test[target], y_pred_test)))

# mae:
print("train mean absolute error:", mean_absolute_error(train[target], y_pred_train))
print("test mean absolute error:", mean_absolute_error(test[target], y_pred_test))

# R^2
print("train R^2:", r2_score(train[target], y_pred_train))
print("test R^2:", r2_score(test[target], y_pred_test))

train root mean squared error: 1127.2749075603413
test root mean squared error: 1108.9539763318812
train mean absolute error: 735.8356346659582
test mean absolute error: 731.9106397906328
train R^2: 0.5907448731405746
test R^2: 0.6043209438936732
